In [2]:
'''Situation des lieux de mesures '''
import polars as pl
import pandas

In [15]:
df = pl.read_csv("datasource/Donnees_changement_climatique-SIM_décadaire/DECAD_SIM2_*.csv.gz", has_header=True, separator=";")

In [6]:
# Workaround SSL error when quering basemap
import os
import certifi
os.environ["REQUESTS_CA_BUNDLE"] = certifi.where()
os.environ["SSL_CERT_FILE"] = certifi.where()

In [7]:
dfp = df.to_pandas();

In [8]:
# Transformation des coordonnées projetées en mètre à partir des hectomètres
dfp["LAMBX"] = dfp["LAMBX"] * 100
dfp["LAMBY"] = dfp["LAMBY"] * 100 

In [9]:
''' les différentes coordonnées (couple X Y sans doublons)'''
dfp["X_Y"] = dfp["LAMBX"].astype("string") + '_' + dfp["LAMBY"].astype("string")
X_Y_unique = dfp["X_Y"].drop_duplicates(inplace=False, ignore_index=True)

X_Y_unique_DF = X_Y_unique.str.rsplit("_", n=1, expand=True)
LAMBX = X_Y_unique_DF.loc[:,[0]].astype(float)
LAMBY = X_Y_unique_DF.loc[:,[1]].astype(float)
LAMBX = LAMBX.values.reshape(9892)
LAMBY = LAMBY.values.reshape(9892)

In [10]:
import geopandas
from shapely.geometry import Point
# Construction de la série des points géographiques dans le systèmes de coordonnées projeté : 'Lambert II étendu'
geometry = geopandas.points_from_xy(x=LAMBX, y=LAMBY, crs="EPSG:27572"  )
geoSerie = geopandas.GeoSeries(data=geometry, crs="EPSG:27572")

# Obtention des points en coordonnées géographiques wgs84 (lat,long)
geoSerie_4326 = geoSerie.to_crs(4326) # wgs84 (lat,long)

# Construction du geoDataframe contenant ces données géographiques en vue de son affichage cartographique.
d = {'X': LAMBX, 'Y' :  LAMBY, 'Lat' : geoSerie_4326.x, 'Long' : geoSerie_4326.y}
df = pandas.DataFrame(d)
gdf = geopandas.GeoDataFrame(df, geometry=geoSerie, crs="EPSG:27572")

In [11]:
'''Situation des lieux de mesures '''
import folium
lon, lat = 1, 46.5 # centre initial de la carte au demarrage
zoom_start = 6
map = folium.Map(
    location=[lat, lon],
    ##crs='EPSG3857',
    tiles="OpenStreetMap",   zoom_start=zoom_start, control_scale=True)
#default implemented tiles :  “OpenStreetMap”, “CartoDB Positron”, “CartoDB Voyager”
    #crs='EPSG:27572', tiles="https://tile.openstreetmap.fr/osmfr/1/1/1.png", attr='My Data Attribution', zoom_start=zoom_start)

gdf.explore (
    m=map,
    color='red',    
)

In [12]:
''' Récupération des adresses correspondantes aux coordonnées géographiques'''
from geopy.geocoders import Nominatim
import geopy
import ssl
## Create an unverified SSL context
gcontext = ssl._create_unverified_context()
ctx = ssl.create_default_context(cafile=certifi.where())

geopy.geocoders.options.default_ssl_context = ctx
geolocator = Nominatim(user_agent="my_geocoder2" , ssl_context = ctx)

In [13]:
from geopy.geocoders import get_geocoder_for_service
get_geocoder_for_service("nominatim")

geopy.geocoders.nominatim.Nominatim

In [14]:
geolocator.reverse((-4.962154433566157, 48.38205706656016),addressdetails=True, zoom=0,)
#df_adress = geopandas.tools.reverse_geocode([Point(-71.0594869, 42.3584697), Point(-77.0365305, 38.8977332)] )

GeocoderUnavailable: HTTPSConnectionPool(host='nominatim.openstreetmap.org', port=443): Max retries exceeded with url: /reverse?lat=-4.962154433566157&lon=48.38205706656016&format=json&addressdetails=1&zoom=0 (Caused by SSLError(SSLCertVerificationError(1, '[SSL: CERTIFICATE_VERIFY_FAILED] certificate verify failed: unable to get local issuer certificate (_ssl.c:1018)')))